In [1]:
import pandas as pd
import numpy as np
import re
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from tensorflow.keras import layers
from tensorflow.keras import models
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from fuzzywuzzy import fuzz
import spacy
import random
from spacy.util import minibatch, compounding
import timeit

C:\ProgramData\Anaconda3\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [73]:
raw_data = pd.read_csv('train.csv')
raw_data['sentiment'].replace({'neutral':0,'negative':-1,'positive':1}, inplace=True)
raw_data


textID                                               text  \
0      cb774db0d1                I`d have responded, if I were going   
1      549e992a42      Sooo SAD I will miss you here in San Diego!!!   
2      088c60f138                          my boss is bullying me...   
3      9642c003ef                     what interview! leave me alone   
4      358bd9e861   Sons of ****, why couldn`t they put them on t...   
...           ...                                                ...   
27476  4eac33d1c0   wish we could come see u on Denver  husband l...   
27477  4f4c4fc327   I`ve wondered about rake to.  The client has ...   
27478  f67aae2310   Yay good for both of you. Enjoy the break - y...   
27479  ed167662a5                         But it was worth it  ****.   
27480  6f7127d9d7     All this flirting going on - The ATG smiles...   

                                           selected_text  sentiment  
0                    I`d have responded, if I were going          0  
1                                               Sooo SAD         -1  
2                                            bullying me         -1  
3                                         leave me alone         -1  
4                                          Sons of ****,         -1  
...                                                  ...        ...  
27476                                             d lost         -1  
27477                                      , don`t force         -1  
27478                          Yay good for both of you.          1  
27479                         But it was worth it  ****.          1  
27480  All this flirting going on - The ATG smiles. Y...          0  

[27481 rows x 4 columns]

In [74]:
raw_data.dropna(inplace=True, axis=0)
raw_data.reset_index(inplace=True)


In [75]:
raw_data.columns

Index(['index', 'textID', 'text', 'selected_text', 'sentiment'], dtype='object')

In [76]:
raw_data

index      textID                                               text  \
0          0  cb774db0d1                I`d have responded, if I were going   
1          1  549e992a42      Sooo SAD I will miss you here in San Diego!!!   
2          2  088c60f138                          my boss is bullying me...   
3          3  9642c003ef                     what interview! leave me alone   
4          4  358bd9e861   Sons of ****, why couldn`t they put them on t...   
...      ...         ...                                                ...   
27475  27476  4eac33d1c0   wish we could come see u on Denver  husband l...   
27476  27477  4f4c4fc327   I`ve wondered about rake to.  The client has ...   
27477  27478  f67aae2310   Yay good for both of you. Enjoy the break - y...   
27478  27479  ed167662a5                         But it was worth it  ****.   
27479  27480  6f7127d9d7     All this flirting going on - The ATG smiles...   

                                           selected_text  sentiment  
0                    I`d have responded, if I were going          0  
1                                               Sooo SAD         -1  
2                                            bullying me         -1  
3                                         leave me alone         -1  
4                                          Sons of ****,         -1  
...                                                  ...        ...  
27475                                             d lost         -1  
27476                                      , don`t force         -1  
27477                          Yay good for both of you.          1  
27478                         But it was worth it  ****.          1  
27479  All this flirting going on - The ATG smiles. Y...          0  

[27480 rows x 5 columns]

In [77]:
def pre_processing(x):
    x = str(x).lower()
    result = []
    for i in x.split(' '):
        if i.find('http') > -1:
            pass
        else:
            if len(i) == 1:
                pass
            else:
                result.append(i)
    x = ' '.join(result)
    REPLACE_BY_SPACE_RE = re.compile('[^0-9a-z# `]')
    x = re.sub('[*.]{2,}',' ',x)
    x = re.sub('\d{1,}',' ',x)
    x = REPLACE_BY_SPACE_RE.sub('', x)
    x = re.sub('\s{2,}',' ',x)
    x = re.sub('\A ','',x)
    return x 
    

In [78]:
raw_data['cleaned_text']= raw_data['selected_text'].apply(lambda x:pre_processing(x))
raw_data['cleaned_text']

0                         i`d have responded if were going
1                                                 sooo sad
2                                              bullying me
3                                           leave me alone
4                                                 sons of 
                               ...                        
27475                                                 lost
27476                                          don`t force
27477                             yay good for both of you
27478                                 but it was worth it 
27479    all this flirting going on the atg smiles yay ...
Name: cleaned_text, Length: 27480, dtype: object

In [79]:
def get_token_ration(x1, x2):
    return fuzz.token_set_ratio(str(x1), str(x2))

In [80]:
ratio_set = []
for i,j in raw_data.loc[:,['cleaned_text','text']].iterrows():
    ratio_set.append(get_token_ration(j[0],j[1]))

In [81]:
raw_data['token_ration'] = ratio_set

In [82]:
raw_data['text'] = raw_data['text'].apply(lambda x: str(x).lower())

In [83]:
raw_data.loc[:,['textID','text','cleaned_text','token_ration','sentiment']]

textID                                               text  \
0      cb774db0d1                i`d have responded, if i were going   
1      549e992a42      sooo sad i will miss you here in san diego!!!   
2      088c60f138                          my boss is bullying me...   
3      9642c003ef                     what interview! leave me alone   
4      358bd9e861   sons of ****, why couldn`t they put them on t...   
...           ...                                                ...   
27475  4eac33d1c0   wish we could come see u on denver  husband l...   
27476  4f4c4fc327   i`ve wondered about rake to.  the client has ...   
27477  f67aae2310   yay good for both of you. enjoy the break - y...   
27478  ed167662a5                         but it was worth it  ****.   
27479  6f7127d9d7     all this flirting going on - the atg smiles...   

                                            cleaned_text  token_ration  \
0                       i`d have responded if were going           100   
1                                               sooo sad           100   
2                                            bullying me           100   
3                                         leave me alone           100   
4                                               sons of            100   
...                                                  ...           ...   
27475                                               lost           100   
27476                                        don`t force           100   
27477                           yay good for both of you           100   
27478                               but it was worth it            100   
27479  all this flirting going on the atg smiles yay ...           100   

       sentiment  
0              0  
1             -1  
2             -1  
3             -1  
4             -1  
...          ...  
27475         -1  
27476         -1  
27477          1  
27478          1  
27479          0  

[27480 rows x 5 columns]

In [84]:
raw_data.drop(raw_data.loc[raw_data['token_ration']<80].index, inplace=True, axis=0)

In [85]:
raw_data['cleaned_text'] = raw_data['cleaned_text'].apply(lambda x : re.sub('[+]\d{2,}',' ',x))

In [86]:
raw_data.isna().sum()

index            0
textID           0
text             0
selected_text    0
sentiment        0
cleaned_text     0
token_ration     0
dtype: int64

In [87]:
raw_data.drop_duplicates(subset='text',keep=False,inplace=True)
raw_data.reset_index(inplace=True)
raw_data

level_0  index      textID  \
0            0      0  cb774db0d1   
1            1      1  549e992a42   
2            2      2  088c60f138   
3            3      3  9642c003ef   
4            4      4  358bd9e861   
...        ...    ...         ...   
26936    27475  27476  4eac33d1c0   
26937    27476  27477  4f4c4fc327   
26938    27477  27478  f67aae2310   
26939    27478  27479  ed167662a5   
26940    27479  27480  6f7127d9d7   

                                                    text  \
0                    i`d have responded, if i were going   
1          sooo sad i will miss you here in san diego!!!   
2                              my boss is bullying me...   
3                         what interview! leave me alone   
4       sons of ****, why couldn`t they put them on t...   
...                                                  ...   
26936   wish we could come see u on denver  husband l...   
26937   i`ve wondered about rake to.  the client has ...   
26938   yay good for both of you. enjoy the break - y...   
26939                         but it was worth it  ****.   
26940     all this flirting going on - the atg smiles...   

                                           selected_text  sentiment  \
0                    I`d have responded, if I were going          0   
1                                               Sooo SAD         -1   
2                                            bullying me         -1   
3                                         leave me alone         -1   
4                                          Sons of ****,         -1   
...                                                  ...        ...   
26936                                             d lost         -1   
26937                                      , don`t force         -1   
26938                          Yay good for both of you.          1   
26939                         But it was worth it  ****.          1   
26940  All this flirting going on - The ATG smiles. Y...          0   

                                            cleaned_text  token_ration  
0                       i`d have responded if were going           100  
1                                               sooo sad           100  
2                                            bullying me           100  
3                                         leave me alone           100  
4                                               sons of            100  
...                                                  ...           ...  
26936                                               lost           100  
26937                                        don`t force           100  
26938                           yay good for both of you           100  
26939                               but it was worth it            100  
26940  all this flirting going on the atg smiles yay ...           100  

[26941 rows x 8 columns]

In [71]:
raw_data.loc[raw_data['text']=='braxton was up at 2:30 untill 4am and now he won`t sleep more than 15 minutes at a time! it`s hard to be a mom on days like this!']

level_0  index      textID  \
10286    10480  10481  a56e55c706   

                                                    text        selected_text  \
10286  braxton was up at 2:30 untill 4am and now he w...  hard to be a mom on   

       sentiment       cleaned_text  token_ration  
10286         -1  hard to be mom on           100

In [88]:
train_dict = {}
def prepare_datset(full_sen, token_sen):
    unique_token = []
    entities = []
    for i in token_sen.split(' '):
        count =0
        for j in unique_token:
            if (i in j) or (j in i):
                count +=1
        if len(i)>1:
            pre = re.search(rf'\b{i}\b',full_sen)
            if pre is None:
                pass
            else:
                if count == 0:
                    if i in unique_token:
                        pass
                    else:
                        if full_sen in train_dict.keys():
                            train_dict[full_sen].append((pre.span()[0],pre.span()[1],'twitter'))
                        else:
                            train_dict[full_sen] = [(pre.span()[0],pre.span()[1],'twitter')]
            unique_token.append(i)
                
                

In [89]:
for i,j in raw_data.loc[:,['text','cleaned_text']].iterrows():
    prepare_datset(j[0],j[1])


In [90]:
train_dict

{' i`d have responded, if i were going': [(1, 4, 'twitter'),
  (5, 9, 'twitter'),
  (10, 19, 'twitter'),
  (21, 23, 'twitter'),
  (26, 30, 'twitter'),
  (31, 36, 'twitter')],
 ' sooo sad i will miss you here in san diego!!!': [(1, 5, 'twitter'),
  (6, 9, 'twitter')],
 'my boss is bullying me...': [(11, 19, 'twitter'), (20, 22, 'twitter')],
 ' what interview! leave me alone': [(17, 22, 'twitter'),
  (23, 25, 'twitter'),
  (26, 31, 'twitter')],
 ' sons of ****, why couldn`t they put them on the releases we already bought': [(1,
   5,
   'twitter'),
  (6, 8, 'twitter')],
 'http://www.dothebouncy.com/smf - some shameless plugging for the best rangers forum on earth': [(33,
   37,
   'twitter'),
  (38, 47, 'twitter'),
  (48, 56, 'twitter'),
  (57, 60, 'twitter'),
  (61, 64, 'twitter'),
  (65, 69, 'twitter'),
  (70, 77, 'twitter'),
  (84, 86, 'twitter'),
  (87, 92, 'twitter')],
 '2am feedings for the baby are fun when he is all smiles and coos': [(30,
   33,
   'twitter')],
 'soooo high': [(

In [91]:
dataset_ = []

In [92]:
for key, value in train_dict.items():
    med_t = (key,{'entities':value})
    dataset_.append(med_t)

In [72]:
pd.DataFrame(dataset_).to_excel('train_2.xlsx')

In [82]:
for texts, annotations in dataset_:
    print(texts)
    print(annotations)

happy mother`s day to all the ladies... with all the moments we cherish with our children, today let those moments cherish you in return.
{'entities': [(0, 5, 'twitter')]}
 hi nick! i really like the serie jonas  it`s awesome! see you soon in the concert! kisses - marta
{'entities': [(41, 45, 'twitter'), (46, 53, 'twitter')]}
 yeah but there are like 5,000 types of snakes..and it`s wicked wicked wicked hot...and idk. i don`t think i`d like it
{'entities': [(95, 100, 'twitter'), (101, 106, 'twitter'), (107, 110, 'twitter'), (20, 24, 'twitter'), (52, 54, 'twitter')]}
at last i wr0te again....got bored the previous dayss....
{'entities': [(29, 34, 'twitter')]}
hey  please reply me, i can`t call you im from mexico and i don`t know the code  love you
{'entities': [(81, 85, 'twitter')]}
arghhh...my korean dvd can`t see..i need to laugh..
{'entities': [(0, 6, 'twitter'), (9, 11, 'twitter'), (12, 18, 'twitter'), (19, 22, 'twitter'), (23, 28, 'twitter'), (29, 32, 'twitter'), (34, 35, 'twitter')

{'entities': [(1, 6, 'twitter'), (9, 14, 'twitter'), (9, 11, 'twitter'), (18, 23, 'twitter'), (24, 30, 'twitter')]}
 the no tweeting guilt trip didn`t stop you huh?  i felt so bad!
{'entities': [(60, 63, 'twitter')]}
just lost internet.  and i was in a raid for 25 os.
{'entities': [(5, 9, 'twitter')]}
back from the gym! i`m no expert or anything, but i`m pretty sure i am not going to be able to move tomorrow, maybe even in a few hours!!
{'entities': [(54, 60, 'twitter'), (61, 65, 'twitter')]}
bah, here i was out in the sun in my new hammock, drinking beer, playing the guitar and singing, and the mosquito chased me inside
{'entities': [(23, 26, 'twitter'), (105, 113, 'twitter'), (114, 120, 'twitter'), (121, 123, 'twitter'), (124, 130, 'twitter')]}
happy mama`s day ladies!  have a good day.
{'entities': [(0, 5, 'twitter')]}
where`s my bus? i want to go home!
{'entities': [(0, 7, 'twitter'), (8, 10, 'twitter'), (11, 14, 'twitter'), (18, 22, 'twitter'), (23, 25, 'twitter'), (26, 28, 'twitt

_**** :o really  well if u want, we can go 2gether next yr?
{'entities': [(7, 8, 'twitter'), (9, 15, 'twitter'), (17, 21, 'twitter'), (22, 24, 'twitter'), (27, 31, 'twitter'), (17, 19, 'twitter'), (36, 39, 'twitter'), (40, 42, 'twitter'), (44, 50, 'twitter'), (51, 55, 'twitter'), (56, 58, 'twitter')]}
 mitchell i tryed to add you on xbox live lastnight during when i was in your live show, but your friends list is full
{'entities': [(1, 9, 'twitter'), (12, 17, 'twitter'), (18, 20, 'twitter'), (21, 24, 'twitter'), (25, 28, 'twitter'), (29, 31, 'twitter'), (32, 36, 'twitter'), (37, 41, 'twitter'), (42, 51, 'twitter'), (52, 58, 'twitter'), (59, 63, 'twitter'), (66, 69, 'twitter'), (55, 57, 'twitter'), (73, 77, 'twitter'), (37, 41, 'twitter'), (83, 87, 'twitter'), (89, 92, 'twitter'), (73, 77, 'twitter'), (98, 105, 'twitter'), (106, 110, 'twitter'), (107, 109, 'twitter'), (114, 118, 'twitter')]}
in bed watching rove
{'entities': [(0, 2, 'twitter'), (3, 6, 'twitter'), (7, 15, 'twitter'), (16

{'entities': [(20, 30, 'twitter'), (31, 39, 'twitter')]}
just watched the goode family premiere online... and i think this may be the last episode i watch. it`s pretty amazingly mediocre  pass.
{'entities': [(111, 120, 'twitter')]}
ugh! i have got to stop biting my nails  grrrrr
{'entities': [(0, 3, 'twitter'), (7, 11, 'twitter'), (12, 15, 'twitter'), (16, 18, 'twitter'), (19, 23, 'twitter'), (24, 30, 'twitter'), (31, 33, 'twitter'), (34, 39, 'twitter'), (41, 47, 'twitter')]}
today was better. my panda can eally cheer me up. i dont know, i am happy, like the legit happy.
{'entities': [(68, 73, 'twitter')]}
f1 & star trek...what a great sunday
{'entities': [(17, 21, 'twitter'), (24, 29, 'twitter'), (30, 36, 'twitter')]}
_leann if it makes you feel better im studying on a sat night w/o blackberries
{'entities': [(28, 34, 'twitter')]}
it was a hard weekend. too much alcohol on these **** 'weinfest'
{'entities': [(9, 13, 'twitter'), (14, 21, 'twitter')]}
_lovato oh i see. thanks for replyi

{'entities': [(17, 21, 'twitter'), (22, 26, 'twitter'), (27, 34, 'twitter')]}
happy mothers day everybody
{'entities': [(0, 5, 'twitter'), (6, 13, 'twitter'), (14, 17, 'twitter'), (18, 27, 'twitter')]}
 thankyou
{'entities': [(1, 9, 'twitter')]}
*cough cough hack hack
{'entities': [(1, 6, 'twitter'), (1, 6, 'twitter'), (13, 17, 'twitter'), (13, 17, 'twitter')]}
almost time to say good bye to my twimulations. i`ll miss my tweeps
{'entities': [(48, 52, 'twitter'), (53, 57, 'twitter'), (31, 33, 'twitter'), (61, 67, 'twitter')]}
regrettin some of the decisions i made
{'entities': [(0, 9, 'twitter')]}
sorry paul scheuring, but prison break series finale sucked... in so many levels
{'entities': [(0, 5, 'twitter'), (6, 10, 'twitter'), (11, 20, 'twitter'), (22, 25, 'twitter'), (26, 32, 'twitter'), (33, 38, 'twitter'), (39, 45, 'twitter'), (46, 52, 'twitter'), (53, 59, 'twitter')]}
i miss my dog  r.i.p.batman... yeah, batman (i really hope `all dogs go to heaven` is true)
{'entities': [(2, 6, '

...

woot. just had my interview! went awsome! i didn`t get to talk with mr. johnny thought...  oh well i still did really good!
{'entities': [(34, 40, 'twitter')]}
 don`t cut yourself!!
{'entities': [(1, 6, 'twitter'), (7, 10, 'twitter'), (11, 19, 'twitter')]}
listening to revenge by kiss to get inspiration... i don`t think kristie is really digging it though
{'entities': [(0, 9, 'twitter'), (10, 12, 'twitter'), (13, 20, 'twitter'), (21, 23, 'twitter'), (24, 28, 'twitter'), (10, 12, 'twitter'), (32, 35, 'twitter'), (36, 47, 'twitter')]}
says i got 2 cards today, from eva n clara. thanks, guys.  http://plurk.com/p/roo6c
{'entities': [(44, 50, 'twitter')]}
getting ready to go to ikea. all alone cuz no one will go with me
{'entities': [(29, 32, 'twitter'), (33, 38, 'twitter'), (39, 42, 'twitter'), (43, 45, 'twitter'), (35, 38, 'twitter'), (50, 54, 'twitter'), (17, 19, 'twitter'), (58, 62, 'twitter'), (63, 65, 'twitter')]}
whoa! twilight the board game! aaahaha
{'entities': [(0, 4, 'twitter'),

{'entities': [(0, 2, 'twitter'), (3, 6, 'twitter'), (7, 9, 'twitter')]}
happy mother`s day to all the moms out there. i hope i never join that crowd
{'entities': [(0, 5, 'twitter'), (6, 14, 'twitter'), (15, 18, 'twitter')]}
just finishing shooting, can u believe it, but got the job done
{'entities': [(43, 46, 'twitter'), (47, 50, 'twitter'), (51, 54, 'twitter'), (55, 58, 'twitter'), (59, 63, 'twitter')]}
 why windows vista
{'entities': [(1, 4, 'twitter'), (5, 12, 'twitter'), (13, 18, 'twitter')]}
 i always have a good day! i make it good all the time but you make it better w/ ur morning greetings!! thank you!!
{'entities': [(17, 21, 'twitter')]}
 is it in crowntown? i think i may just meet you there? let me get ready and ill let you know
{'entities': [(1, 3, 'twitter'), (4, 6, 'twitter'), (7, 9, 'twitter'), (10, 19, 'twitter'), (23, 28, 'twitter'), (31, 34, 'twitter'), (35, 39, 'twitter'), (40, 44, 'twitter'), (45, 48, 'twitter'), (49, 54, 'twitter'), (56, 59, 'twitter'), (40, 42, 'twi

goodnight
{'entities': [(0, 9, 'twitter')]}
graveyard charged my card twice (one correct total, one random amt) from last night`s #atltweet tweetup. check your accounts!
{'entities': [(0, 9, 'twitter'), (10, 17, 'twitter'), (18, 20, 'twitter'), (21, 25, 'twitter'), (26, 31, 'twitter'), (33, 36, 'twitter'), (37, 44, 'twitter'), (45, 50, 'twitter'), (33, 36, 'twitter'), (56, 62, 'twitter'), (63, 66, 'twitter'), (68, 72, 'twitter'), (73, 77, 'twitter'), (78, 85, 'twitter'), (86, 95, 'twitter'), (96, 103, 'twitter'), (105, 110, 'twitter'), (111, 115, 'twitter'), (116, 124, 'twitter')]}
 freeeeeeeeeeeeeeeezing **** im so excited to see you soooooooon!!!  lets go see 17 again again yehhaaaaaaa!
{'entities': [(1, 23, 'twitter'), (29, 31, 'twitter'), (32, 34, 'twitter'), (35, 42, 'twitter'), (43, 45, 'twitter'), (46, 49, 'twitter'), (50, 53, 'twitter'), (54, 64, 'twitter'), (69, 73, 'twitter'), (74, 76, 'twitter'), (46, 49, 'twitter'), (84, 89, 'twitter'), (84, 89, 'twitter'), (96, 107, 'twitt

{'entities': [(3, 7, 'twitter'), (8, 10, 'twitter'), (11, 14, 'twitter'), (15, 18, 'twitter'), (19, 27, 'twitter')]}
looking for a vibrating phone is like trying to find 'a feeling.'
{'entities': [(0, 7, 'twitter'), (8, 11, 'twitter'), (14, 23, 'twitter'), (24, 29, 'twitter'), (30, 32, 'twitter'), (33, 37, 'twitter'), (38, 44, 'twitter'), (45, 47, 'twitter'), (48, 52, 'twitter'), (12, 13, 'twitter'), (56, 63, 'twitter')]}
_in_forks ::static:: i know! i`ve barely seen anyone since i got into paris yesterday.  i`ve just been walking around.  ::static::
{'entities': [(12, 18, 'twitter'), (23, 27, 'twitter'), (29, 33, 'twitter'), (34, 40, 'twitter'), (41, 45, 'twitter'), (46, 52, 'twitter'), (53, 58, 'twitter'), (61, 64, 'twitter'), (65, 69, 'twitter'), (70, 75, 'twitter'), (76, 85, 'twitter'), (29, 33, 'twitter'), (93, 97, 'twitter'), (98, 102, 'twitter'), (103, 110, 'twitter'), (111, 117, 'twitter'), (12, 18, 'twitter')]}
wants to meet jeff hardy and beth britt so bad its soo annoying  x

: i miss you
{'entities': [(4, 8, 'twitter')]}
my phone works! its whack. well good morning. gonna go eat breakfast with neil before school starts
{'entities': [(0, 2, 'twitter'), (3, 8, 'twitter'), (9, 14, 'twitter'), (16, 19, 'twitter'), (20, 25, 'twitter'), (27, 31, 'twitter'), (32, 36, 'twitter'), (37, 44, 'twitter')]}
you guys dont get too drunk without me
{'entities': [(0, 3, 'twitter'), (4, 8, 'twitter'), (9, 13, 'twitter'), (14, 17, 'twitter'), (18, 21, 'twitter'), (22, 27, 'twitter'), (28, 35, 'twitter'), (36, 38, 'twitter')]}
 he didn`t know there was going to be a test
{'entities': [(1, 3, 'twitter'), (4, 10, 'twitter'), (11, 15, 'twitter'), (16, 21, 'twitter'), (22, 25, 'twitter'), (26, 31, 'twitter'), (32, 34, 'twitter'), (35, 37, 'twitter'), (40, 44, 'twitter')]}
shack idol today(: can`t wait. it`s gonna be funnn poor cameron. he fell on a bar in speech today. i felt so bad for him
{'entities': [(0, 5, 'twitter'), (6, 10, 'twitter'), (11, 16, 'twitter'), (19, 24, 'twitter

In [93]:
def main(model=None, output_dir=None, n_iter=20,TRAIN_DATA=None):
    nlp = spacy.blank("en")  # create blank Language class
    print("Created blank 'en' model")
    print('Checking NER pipe in model')
    if "ner" not in nlp.pipe_names:
        ner = nlp.create_pipe("ner")
        nlp.add_pipe(ner, last=True)

    print('Adding Entries')
    for _, annotations in TRAIN_DATA:
        for ent in annotations.get("entities"):
            ner.add_label(ent[2])

    # get names of other pipes to disable them during training
    other_pipes = [pipe for pipe in nlp.pipe_names if pipe != 'ner']
    with nlp.disable_pipes(*other_pipes):  # only train NER
        print('Traning of NER Started')
        # reset and initialize the weights randomly – but only if we're
        # training a new model
        if model is None:
            optimi = nlp.begin_training()
        for itn in range(n_iter):
            print('Starting with Iteration {}'.format(itn))
            random.shuffle(TRAIN_DATA)
            losses = {}
            # batch up the examples using spaCy's minibatch
            batches = minibatch(TRAIN_DATA, size=compounding(4.0, 32.0, 1.001))
            for batch in batches:
                texts, annotations = zip(*batch)
                nlp.update(
                    texts,  # batch of texts
                    annotations,  # batch of annotations
                    drop=0.3,  # dropout - make it harder to memorise data
                    sgd = optimi,
                    losses=losses,
                )
            print("Losses", losses)
    nlp.to_disk(output_dir)
    print("Saved model to", output_dir)

In [94]:
main(None,r'C:\Users\HP\AI Projects\Learn\Kaggle\twitter_analysis',100,dataset_)

Created blank 'en' model
Checking NER pipe in model
Adding Entries
Traning of NER Started
Starting with Iteration 0
Losses {'ner': 135234.77241668105}
Starting with Iteration 1
Losses {'ner': 121641.31846480738}
Starting with Iteration 2
Losses {'ner': 116713.5159198243}
Starting with Iteration 3
Losses {'ner': 113342.92660007489}
Starting with Iteration 4
Losses {'ner': 111694.71145041933}
Starting with Iteration 5
Losses {'ner': 109291.22451754777}
Starting with Iteration 6
Losses {'ner': 107425.04199852797}
Starting with Iteration 7
Losses {'ner': 105699.80831430489}
Starting with Iteration 8
Losses {'ner': 103649.25883527589}
Starting with Iteration 9
Losses {'ner': 102446.49315057113}
Starting with Iteration 10
Losses {'ner': 100857.65901214325}
Starting with Iteration 11
Losses {'ner': 99661.82445755244}
Starting with Iteration 12
Losses {'ner': 98229.55599249744}
Starting with Iteration 13
Losses {'ner': 96361.74549447914}
Starting with Iteration 14
Losses {'ner': 95527.91426606

In [95]:
nlp_new = spacy.load(r'C:\Users\HP\AI Projects\Learn\Kaggle\twitter_analysis')


In [101]:
dat = nlp_new('omg. cat had a hairball. awake now.')
for ent in dat.ents:
    print(ent)

omg


In [97]:
raw_data.loc[raw_data['text']=='thanx sis i`ll b sure to let them know how many people r praying w/them...']

Empty DataFrame
Columns: [level_0, index, textID, text, selected_text, sentiment, cleaned_text, token_ration]
Index: []